# Working with Networks - Quickstart
## OpenStreetMap - Shortest Paths - Reachable Areas

In this notebook we want to play around with the osmnx and networkx libraries. In specific we will see how we load OpenStreetMap data, get locations of amenities e.g. restaurants and calculate routes and walking distances to this restaurants.

First we start with the import of all different libraries we are going to use:

In [1]:
import geopandas as gpd
import shapely
import folium
import matplotlib.pyplot as plt
import osmnx as ox
import networkx as nx
import numpy as np
import os

Then we have to import our study area. For this example we will use Bremen and in particular the district Westend again. Note that we will work with Coordinate Reference Systems (CRS) in this example. There a thousands, of different reference systems but gladly we can differ them by unique, numerical, so called epsg-codes. We will need two types of reference systems: 

1: The WGS84 - World Geodetic System 1984 which is also used for GPS and OSM for example. It is based on latitude and longitude in degrees. The epsg code is 4326.

2: The ETRS89-extended / LAEA Europe System, which is a projected reference system in meters focused on the european continent. The epsg code is 3035.

Firstly lets import and check the projection of our study area:

In [2]:
#os.chdir("...")
bremen = gpd.read_file("../data_example/Example_Bremen_Neighborhoods.gpkg")
bremen.crs

<Derived Projected CRS: EPSG:3035>
Name: ETRS89-extended / LAEA Europe
Axis Info [cartesian]:
- Y[north]: Northing (metre)
- X[east]: Easting (metre)
Area of Use:
- name: Europe - European Union (EU) countries and candidates. Europe - onshore and offshore: Albania; Andorra; Austria; Belgium; Bosnia and Herzegovina; Bulgaria; Croatia; Cyprus; Czechia; Denmark; Estonia; Faroe Islands; Finland; France; Germany; Gibraltar; Greece; Hungary; Iceland; Ireland; Italy; Kosovo; Latvia; Liechtenstein; Lithuania; Luxembourg; Malta; Monaco; Montenegro; Netherlands; North Macedonia; Norway including Svalbard and Jan Mayen; Poland; Portugal including Madeira and Azores; Romania; San Marino; Serbia; Slovakia; Slovenia; Spain including Canary Islands; Sweden; Switzerland; Turkey; United Kingdom (UK) including Channel Islands and Isle of Man; Vatican City State.
- bounds: (-35.58, 24.6, 44.83, 84.73)
Coordinate Operation:
- name: Europe Equal Area 2001
- method: Lambert Azimuthal Equal Area
Datum: Europ

We see that the projection of our study area is in ETRS89 with the epsg code 3035. But since OSM works with the WGS 84 - epsg:4326 we have to reproject our file. Then we select only the district of Westend and create a starting point for the routing algorithms. Also note that there is a difference between a GeoSeries and a GeoDataFrame.

In [3]:
bremen = bremen.to_crs(epsg = 4326)
westend = bremen.loc[bremen.Neighborhood_Name == "Westend"]
start_point = gpd.GeoSeries(shapely.Point([8.788266, 53.094551]))

Next we need amenities were we want to go. Let's say we are hungry and want to visit a restaurant. So we can aquire all restaurants of the district Westend. We also need to check the shape of the dataframe and its CRS.

In [4]:
restaurants = ox.geometries.geometries_from_polygon(polygon = westend.geometry.iloc[0],
                                                         tags = {"amenity":"restaurant"})

print(restaurants.shape)
restaurants.crs

(9, 24)


<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

The Dataframe has 9 rows or 9 restaurants in it with 24 attribute columns in it. The reason why we only get 9 restaurants is because OSM is very specific. For bars, cafes, or fast food restaurants there are extra amenity tags.

We also see that the restaurant dataframe is in the right projection: epsg:4326. We can start work with it.

Routing algorithms are based on networks or so called graphs. With the osmnx library we can import a street network or street graph for our area of interest. In this example we will use a specific network for pedestrians. 

A graph contains nodes which are connected trough edges. To display them and work with them we have to convert them to geodataframes:

In [5]:
G = ox.graph_from_polygon(westend.geometry.iloc[0], network_type = "walk", simplify = False)
graph_nodes, graph_edges = ox.graph_to_gdfs(G)

Now let's visualize all we have. We will again use folium maps and the geopandas.explore() function. We will see all streets (edges) and restaurants which are mapped in the OSM. We also want to display the nodes of the network into our map.

In [14]:
m = westend.explore( name="Westend", tooltip = False, popup = False, highlight = False,
                    style_kwds=dict(color="red",weight=2, opacity=1, fillOpacity=0))

m = graph_edges.explore(m=m, color="blue", name="Streets")
m = graph_nodes.explore(m=m, color = "blue", name = "Nodes")
m = start_point.explore(m=m, color = "green", name = "Start Point", marker_kwds=dict(radius=7))
m = restaurants.explore(m=m, color = "yellow", name = "Restaurants", marker_kwds=dict(radius=7))
folium.LayerControl().add_to(m)
m

So now lets say we are hungry and lazy. We want food and we don't want to go further than 350 meters. Let's find all restaurants in 350 walking distance. For this we will need a subgraph based on our original graph. Also we have to find the nearest node in the graph to our starting point.

In [15]:
start_node = start_point.iloc[0]
start_id = ox.nearest_nodes(G, start_node.x, start_node.y) 

# Create subraph with max 5 mins. from point
subgraph = nx.ego_graph(G, start_id, radius = 350, distance = "length")
subgraph_nodes, subgraph_edges = ox.graph_to_gdfs(subgraph)

Now we want all restaurant in this 350m. walking distance. For that we have to convert the subgraph into an real area. We create a convex hull around all points in the network and then clip the restaurants to this walkable area.

In [16]:
walkable_area = subgraph_nodes.unary_union.convex_hull
reachable_restaurants = restaurants.clip(walkable_area)
print("There are {} restaurants in 350m walking distance.".format(reachable_restaurants.shape[0]))

There are 5 restaurants in 350m walking distance.


So in walking distance there a only 5 restaurants. Let's display them in the map in combination with the walkable streets:

In [17]:
m = westend.explore(height=500, width=1000, name="Westend", tooltip = False, popup = False, highlight = False,
                    style_kwds=dict(color="red",weight=2, opacity=1, fillOpacity=0))

m = graph_edges.explore(m=m, color="blue", name="Streets")
m = subgraph_edges.explore(m = m, name="Walkable Path", color = "yellow" )
m = reachable_restaurants.explore(m=m, color = "yellow", name = "Restaurants", marker_kwds=dict(radius=7))
m = start_point.explore(m=m, color = "green", name = "Start Point", marker_kwds=dict(radius=7))
folium.LayerControl().add_to(m)
m

Now we want to get the walking route from our start point to all the restaurants and pick the shortest. For that we iterate over all restaurant points und use the networkx function shortest_path(). As origin we use our starting point and  as destination we use the point geometry of the current restaurant. Before that we again have to get the nearest node to it in our graph.
The shortest_path function gives as a sequence of the node ids as integer values of the network. To retrieve the route we have index them from the nodes of the graph. Finallye we convert them to LineStrings and append all of them into a list.

In [18]:
routes_list = []
for idx,restaurant in reachable_restaurants.iterrows():
    dest_id = ox.nearest_nodes(G, restaurant.geometry.x, restaurant.geometry.y)
    route = nx.shortest_path(G, start_id, dest_id, weight = "length")
    route_points = graph_nodes.loc[route]
    route_line = shapely.LineString(list(route_points.geometry.values))
    routes_list.append(route_line)

To get the distances of the different routes we have to convert the list into a geodataframe. Note that we just copy our restaurant dataframe but set als geometry the LineString list. Also the calculation was done in the epsg:4326 so we also have to set the dataframe to this CRS.

But as we already know the units of WGS84 - epsg:4326 are in degrees of latitude and longitude. To get the distance in meters we have to reproject the dataframe into a projected coordinate system, which uses meters as units. One example for this is the epsg:3035. 

In [19]:
restaurant_routes = gpd.GeoDataFrame(data = reachable_restaurants.copy(), geometry = routes_list, crs = "epsg:4326")
restaurant_routes.to_crs(3035, inplace = True)

After that we set a new column called distance with .length and get the minimum value of this column.

In [20]:
restaurant_routes["Distance"] = restaurant_routes.length
shortest_route = restaurant_routes.loc[restaurant_routes.Distance == np.min(restaurant_routes.Distance)]

print("The shortest walking distance to the nearest restaurant is {} meters.".format(round(shortest_route.Distance.item(),1)))

The shortest walking distance to the nearest restaurant is 224.3 meters.


Finally we can display the shortest route to the next restaurant in our map:

In [21]:
m = westend.explore(height=500, width=1000, name="Westend", tooltip = False, popup = False, highlight = False,
                    style_kwds=dict(color="red",weight=2, opacity=1, fillOpacity=0))
m = shortest_route.explore(m = m, name="Shortest Route", style_kwds=dict(color="blue",weight=3) )
m = reachable_restaurants.explore(m=m, color = "blue", name = "Restaurants", marker_kwds=dict(radius=7))
m = start_point.explore(m=m, color = "green", name = "Start Point", marker_kwds=dict(radius=7))

folium.LayerControl().add_to(m)
m